In [1]:
from flood_forecast.trainer import train_function

In [2]:
import os 

In [3]:
import wandb

In [4]:
%matplotlib inline

In [5]:
os.getcwd() + '/Transformer_flow_forecasting.ipynb'

'/media/xsy/pytorch-forecasting/docs/source/tutorials/Transformer_flow_forecasting.ipynb'

In [6]:
import os
os.environ['WANDB_NOTEBOOK_NAME'] = os.getcwd() + '/Transformer_flow_forecasting.ipynb'

In [7]:
import logging

logger = logging.getLogger("wandb")
logger.setLevel(logging.ERROR)

In [8]:
!pip install wandb -qqq

In [9]:
wandb.login()

wandb: Currently logged in as: xuesyn (use `wandb login --relogin` to force relogin)


True

In [10]:
from datetime import datetime
import pandas as pd
testgx8doct = pd.read_csv("./xj/test_gx_8d_Oct.csv")
st = []
for indx, dt in enumerate(testgx8doct['datetime']):
    dtn = datetime.strptime(dt,"%Y/%m/%d %H:%M")
    if ((dtn.hour == 5) or (dtn.hour == 6) or (dtn.hour == 7)) and (indx >= 160) and (len(testgx8doct) - indx >= 169):
        st.append(dt)
        #print(indx)
#datetime.strptime("2020/04/02 16:00","%Y/%m/%d %H:%M").hour

In [11]:
def make_config_file(file_path, test_path, train_end, valid_end):
  run = wandb.init(project="xinjiang_goldwind_gpu_train_729_test_oct_8")
  wandb_config = wandb.config
  config_default={                 
    "model_name": "CustomTransformerDecoder",
    "model_type": "PyTorch",
    "model_params": {
      "n_time_series":577,
      "seq_length":160, 
      "output_seq_length":wandb_config["out"],
      "d_model":wandb_config["embeddingdim"],
      "n_heads":8,
      "dropout":wandb_config["dropout"],
      "forward_dim":wandb_config["forwarddim"],
     },
    "dataset_params":
    {  "class": "default",
       "training_path": file_path,
       "validation_path": file_path,
       "test_path": test_path,
       "batch_size":wandb_config["batchsize"],
       "forecast_history":160,
       "forecast_length":wandb_config["out"],
       "pin_memory":True,
       "train_end": train_end,
       "valid_start":int(train_end+1),
       "valid_end": int(valid_end),
       "test_start": 0,
       "target_col": ["OT"],
       "relevant_cols": ["OT"] + [str(x) for x in range((576))],
       "scaler": "StandardScaler", 
       "interpolate": False
    },
    "early_stopping":
    {
       "patience":wandb_config["es"]

    },
    "training_params":
    {
       "criterion":"MSE",
       "optimizer": "Adam",
       "optim_params":
       {
       },
       "lr": wandb_config["lr"],
       "epochs": 64,
       "batch_size":wandb_config["batchsize"],
       "device":"cuda",
    },
    "GCS": False,
    "sweep":True,
    "wandb":False,
    "device":"cuda",
   "metrics":["RMSE"],
   "inference_params":
   {     
         "datetime_start":st,
          "hours_to_forecast":168, 
          "test_csv_path":test_path,
          "decoder_params":{
              "decoder_function": "simple_decode", 
            "unsqueeze_dim": 1,
              "device":"cuda",
          },
          "dataset_params":{
             "file_path": test_path,
             "forecast_history":160,
             "forecast_length":wandb_config["out"],
             "relevant_cols": ["OT"] + [str(x) for x in range((576))],
             "target_col": ["OT"],
             "scaling": "StandardScaler",
             "interpolate_param": False,
             "seperate_training_and_validation": True, 
          }
      }
  }
  wandb.config.update(config_default)
  return config_default

In [12]:
sweep_config = {
  "name": "Default sweep",
  "method": "random",
  "parameters": {
        "lr":{
            "values":[0.1,0.001]
        },
        "out":{
            "values":[168,160]
        },
        "embeddingdim":{
            "values":[128,64]
        },
        "dropout":{
            "values":[0.5,0.3,0.1,0.001]
        },
        "forwarddim":{
            "values":[2048,1024]
        },
        "batchsize":{
            "values":[64,40,20,10]
        },
        "es":{
            "values":[4,3]
        },
    }
}

In [ ]:
from flood_forecast.trainer import train_function
import wandb
sweep_id = wandb.sweep(sweep_config)
os.environ["SWEEP_ID"] = sweep_id
#!wandb agent $SWEEP_ID
wandb.agent(sweep_id, lambda: train_function("PyTorch", make_config_file("./xj/train_gx_6m_7to9.csv","./xj/test_gx_8d_Oct.csv", 6000, 7103)) )
#_secretagent(sweep_id, lambda: train_function("PyTorch", make_config_file("train.csv", 4500, 6000)))

Create sweep with ID: 75hcspme
Sweep URL: https://wandb.ai/xuesyn/uncategorized/sweeps/75hcspme


wandb: Agent Starting Run: yyaddbhs with config:
wandb: 	batchsize: 40
wandb: 	dropout: 0.1
wandb: 	embeddingdim: 64
wandb: 	es: 3
wandb: 	forwarddim: 2048
wandb: 	lr: 0.001
wandb: 	out: 160
wandb: WARNING Ignored wandb.init() arg project when running a sweep
wandb: wandb version 0.10.32 is available!  To upgrade, please run:
wandb:  $ pip install wandb --upgrade


interpolate should be below
[]
Now loading ./xj/train_gx_6m_7to9.csv
scaling now
interpolate should be below
[]
Now loading ./xj/train_gx_6m_7to9.csv
scaling now
interpolate should be below
[]
Now loading ./xj/test_gx_8d_Oct.csv
scaling now
Using Wandb config:
{'batchsize': 40, 'dropout': 0.1, 'embeddingdim': 64, 'es': 3, 'forwarddim': 2048, 'lr': 0.001, 'out': 160, 'model_name': 'CustomTransformerDecoder', 'model_type': 'PyTorch', 'model_params': {'n_time_series': 577, 'seq_length': 160, 'output_seq_length': 160, 'd_model': 64, 'n_heads': 8, 'dropout': 0.1, 'forward_dim': 2048}, 'dataset_params': {'class': 'default', 'training_path': './xj/train_gx_6m_7to9.csv', 'validation_path': './xj/train_gx_6m_7to9.csv', 'test_path': './xj/test_gx_8d_Oct.csv', 'batch_size': 40, 'forecast_history': 160, 'forecast_length': 160, 'pin_memory': True, 'train_end': 6000, 'valid_start': 6001, 'valid_end': 7103, 'test_start': 0, 'target_col': ['OT'], 'relevant_cols': ['OT', '0', '1', '2', '3', '4', '5', '

wandb: Agent Starting Run: b4qtfa1k with config:
wandb: 	batchsize: 10
wandb: 	dropout: 0.001
wandb: 	embeddingdim: 64
wandb: 	es: 4
wandb: 	forwarddim: 1024
wandb: 	lr: 0.1
wandb: 	out: 168
wandb: WARNING Ignored wandb.init() arg project when running a sweep
wandb: wandb version 0.10.32 is available!  To upgrade, please run:
wandb:  $ pip install wandb --upgrade


interpolate should be below
[]
Now loading ./xj/train_gx_6m_7to9.csv
scaling now
interpolate should be below
[]
Now loading ./xj/train_gx_6m_7to9.csv
scaling now
interpolate should be below
[]
Now loading ./xj/test_gx_8d_Oct.csv
scaling now
Using Wandb config:
{'batchsize': 10, 'dropout': 0.001, 'embeddingdim': 64, 'es': 4, 'forwarddim': 1024, 'lr': 0.1, 'out': 168, 'model_name': 'CustomTransformerDecoder', 'model_type': 'PyTorch', 'model_params': {'n_time_series': 577, 'seq_length': 160, 'output_seq_length': 168, 'd_model': 64, 'n_heads': 8, 'dropout': 0.001, 'forward_dim': 1024}, 'dataset_params': {'class': 'default', 'training_path': './xj/train_gx_6m_7to9.csv', 'validation_path': './xj/train_gx_6m_7to9.csv', 'test_path': './xj/test_gx_8d_Oct.csv', 'batch_size': 10, 'forecast_history': 160, 'forecast_length': 168, 'pin_memory': True, 'train_end': 6000, 'valid_start': 6001, 'valid_end': 7103, 'test_start': 0, 'target_col': ['OT'], 'relevant_cols': ['OT', '0', '1', '2', '3', '4', '5',

...

Run jkbuug0r errored: RuntimeError('CUDA out of memory. Tried to allocate 2.00 MiB (GPU 0; 10.92 GiB total capacity; 3.29 GiB already allocated; 4.50 MiB free; 3.30 GiB reserved in total by PyTorch)')
wandb: ERROR Run jkbuug0r errored: RuntimeError('CUDA out of memory. Tried to allocate 2.00 MiB (GPU 0; 10.92 GiB total capacity; 3.29 GiB already allocated; 4.50 MiB free; 3.30 GiB reserved in total by PyTorch)')
wandb: Agent Starting Run: gmrwsflh with config:
wandb: 	batchsize: 64
wandb: 	dropout: 0.001
wandb: 	embeddingdim: 128
wandb: 	es: 4
wandb: 	forwarddim: 1024
wandb: 	lr: 0.1
wandb: 	out: 168
wandb: WARNING Ignored wandb.init() arg project when running a sweep
wandb: wandb version 0.10.32 is available!  To upgrade, please run:
wandb:  $ pip install wandb --upgrade


Run gmrwsflh errored: RuntimeError('CUDA out of memory. Tried to allocate 2.00 MiB (GPU 0; 10.92 GiB total capacity; 3.29 GiB already allocated; 4.50 MiB free; 3.30 GiB reserved in total by PyTorch)')
wandb: ERROR Run gmrwsflh errored: RuntimeError('CUDA out of memory. Tried to allocate 2.00 MiB (GPU 0; 10.92 GiB total capacity; 3.29 GiB already allocated; 4.50 MiB free; 3.30 GiB reserved in total by PyTorch)')
wandb: Agent Starting Run: 0xne5cbc with config:
wandb: 	batchsize: 64
wandb: 	dropout: 0.3
wandb: 	embeddingdim: 64
wandb: 	es: 4
wandb: 	forwarddim: 2048
wandb: 	lr: 0.001
wandb: 	out: 160
wandb: WARNING Ignored wandb.init() arg project when running a sweep
wandb: wandb version 0.10.32 is available!  To upgrade, please run:
wandb:  $ pip install wandb --upgrade


Run 0xne5cbc errored: RuntimeError('CUDA out of memory. Tried to allocate 2.00 MiB (GPU 0; 10.92 GiB total capacity; 3.29 GiB already allocated; 4.50 MiB free; 3.30 GiB reserved in total by PyTorch)')
wandb: ERROR Run 0xne5cbc errored: RuntimeError('CUDA out of memory. Tried to allocate 2.00 MiB (GPU 0; 10.92 GiB total capacity; 3.29 GiB already allocated; 4.50 MiB free; 3.30 GiB reserved in total by PyTorch)')
wandb: Agent Starting Run: x4kejd1u with config:
wandb: 	batchsize: 64
wandb: 	dropout: 0.001
wandb: 	embeddingdim: 64
wandb: 	es: 3
wandb: 	forwarddim: 1024
wandb: 	lr: 0.001
wandb: 	out: 168
wandb: WARNING Ignored wandb.init() arg project when running a sweep
wandb: wandb version 0.10.32 is available!  To upgrade, please run:
wandb:  $ pip install wandb --upgrade


Run x4kejd1u errored: RuntimeError('CUDA out of memory. Tried to allocate 2.00 MiB (GPU 0; 10.92 GiB total capacity; 3.29 GiB already allocated; 4.50 MiB free; 3.30 GiB reserved in total by PyTorch)')
wandb: ERROR Run x4kejd1u errored: RuntimeError('CUDA out of memory. Tried to allocate 2.00 MiB (GPU 0; 10.92 GiB total capacity; 3.29 GiB already allocated; 4.50 MiB free; 3.30 GiB reserved in total by PyTorch)')
wandb: Agent Starting Run: zj23qdvy with config:
wandb: 	batchsize: 64
wandb: 	dropout: 0.1
wandb: 	embeddingdim: 64
wandb: 	es: 3
wandb: 	forwarddim: 1024
wandb: 	lr: 0.001
wandb: 	out: 160
wandb: WARNING Ignored wandb.init() arg project when running a sweep
wandb: wandb version 0.10.32 is available!  To upgrade, please run:
wandb:  $ pip install wandb --upgrade


Run zj23qdvy errored: RuntimeError('CUDA out of memory. Tried to allocate 2.00 MiB (GPU 0; 10.92 GiB total capacity; 3.29 GiB already allocated; 4.50 MiB free; 3.30 GiB reserved in total by PyTorch)')
wandb: ERROR Run zj23qdvy errored: RuntimeError('CUDA out of memory. Tried to allocate 2.00 MiB (GPU 0; 10.92 GiB total capacity; 3.29 GiB already allocated; 4.50 MiB free; 3.30 GiB reserved in total by PyTorch)')
wandb: Agent Starting Run: d9qenr0f with config:
wandb: 	batchsize: 10
wandb: 	dropout: 0.1
wandb: 	embeddingdim: 128
wandb: 	es: 3
wandb: 	forwarddim: 2048
wandb: 	lr: 0.1
wandb: 	out: 160
wandb: WARNING Ignored wandb.init() arg project when running a sweep
wandb: wandb version 0.10.32 is available!  To upgrade, please run:
wandb:  $ pip install wandb --upgrade


In [ ]:
def make_config_file(file_path, train_end, valid_end):
  run = wandb.init(project="xinjiang_goldwind_gpu_test")
  wandb_config = wandb.config
  config_default={                 
    "model_name": "SimpleTransformer",
    "model_type": "PyTorch",
    "model_params": {
      "number_time_series":577,
      "seq_length":160, 
      "output_seq_len":168,
      "d_model":128,
      "n_heads":8,
      "dropout":0.1,
      "forward_dim":2048,
      "sigmoid":False,
     },
    "dataset_params":
    {  "class": "default",
       "training_path": file_path,
       "validation_path": file_path,
       "test_path": "./xj/test_trial.csv",
       "batch_size":64,
       "forecast_history":160,
       "forecast_length":168,
       "pin_memory":True,
       "train_end": train_end,
       "valid_start":int(train_end+1),
       "valid_end": int(valid_end),
       "test_start": 0,
       "target_col": ["OT"],
       "relevant_cols": ["OT"] + [str(x) for x in range((576))],
       "scaler": "StandardScaler", 
       "interpolate": False
    },
    "early_stopping":
    {
       "patience":5

    },
    "takes_target": True,
    "training_params":
    {
       "criterion":"RMSE",
       "optimizer": "Adam",
       "optim_params":
       {
       },
       "lr": 0.3,
       "epochs": 2,
       "batch_size":64,
       "device":"cuda",
    },
    "GCS": False,
    "sweep":True,
    "wandb":False,
    "device":"cuda",
    "forward_params":{
        "t":{}
    },
   "metrics":["RMSE"],
   "inference_params":
   {     
         "datetime_start":"2020/10/02 18:15",
          "hours_to_forecast":168, 
          "test_csv_path":"./xj/test_trial.csv",
          "decoder_params":{
              "decoder_function": "simple_decode", 
            "unsqueeze_dim": 1,
              "device":"cuda",
          },
          "dataset_params":{
             "file_path": "./xj/test_trial.csv",
             "forecast_history":160,
             "forecast_length":168,
             "relevant_cols": ["OT"] + [str(x) for x in range((576))],
             "target_col": ["OT"],
             "scaling": "StandardScaler",
             "interpolate_param": False
          }
      }
  }
  wandb.config.update(config_default)
  return config_default

In [ ]:
def make_config_file(file_path, train_end, valid_end):
  run = wandb.init(project="xinjiang_goldwind")
  wandb_config = wandb.config
  config_default={                 
    "model_name": "CustomTransformerDecoder",
    "model_type": "PyTorch",
    "model_params": {
      "n_time_series":16,
      "seq_length":160, 
      "output_seq_length":168,
      "d_model":577,
     },
    "dataset_params":
    {  "class": "default",
       "training_path": file_path,
       "validation_path": file_path,
       "test_path": "./xj/test_gx_8d.csv",
       "batch_size":wandb_config["batch_size"],
       "forecast_history":wandb_config["forecast_history"],
       "forecast_length":168,
       "train_end": train_end,
       "valid_start":int(train_end+1),
       "valid_end": int(valid_end),
       "test_start": 0,
       "target_col": ["OT"],
       "relevant_cols": ["OT"] + [str(x) for x in range((576))],
       "scaler": "StandardScaler", 
       "interpolate": False
    },
    "early_stopping":
    {
       "patience":3

    },
    "training_params":
    {
       "criterion":"MSE",
       "optimizer": "Adam",
       "optim_params":
       {
       },
       "lr": 0.3,
       "epochs": 4,
       "batch_size":4
    
    },
    "GCS": True,
    "sweep":True,
    "wandb":False,
    "forward_params":{},
   "metrics":["MSE"],
   "inference_params":
   {     
         "datetime_start":"2020-07-01",
          "hours_to_forecast":42, 
          "test_csv_path":file_path,
          "decoder_params":{
              "decoder_function": "simple_decode", 
            "unsqueeze_dim": 1
          },
          "dataset_params":{
             "file_path": file_path,
             "forecast_history":wandb_config["forecast_history"],
             "forecast_length":168,
             "relevant_cols": ["OT"] + [str(x) for x in range((576))],
             "target_col": ["OT"],
             "scaling": "StandardScaler",
             "interpolate_param": False
          }
      }
  }
  wandb.config.update(config_default)
  return config_default